# RWKV v5-headsize2x / embedding init-range 1e-01 / 4k

- 6 layers
- 4096 embedding size

Going through the modified memory training for v5 models, across various initial embedding model weights

**Note:** This project assumes you have the rwkv-infctx conda env setup

# Basic Setup

In [1]:
# First lets setup the various directories, and init the model
!mkdir -p ../../../../model/
!mkdir -p ../../../../datapath/
!mkdir -p ../../../../checkpoint/

In [2]:
# Additional dependencies for eval stuff
!pip install -q aiocsv aiofiles


[notice] A new release of pip is available: 23.1.2 -> 23.2.1
[notice] To update, run: python3.11 -m pip install --upgrade pip


In [3]:
DEEPSPEED_STRAT="deepspeed_stage_2_offload"
GPU_DEVICES="auto"
ENABLE_WANDB=True

RWKV_WAVENET_LAYERS=1

EMBED_SCALE=0.1
EMBED_SCALE_LABEL=str(EMBED_SCALE).replace(".", "_")

LAYER_COUNT=6
EMBED_DIM=4096

WANDB_PREFIX=f"v5-hs2x-L{LAYER_COUNT}-D{EMBED_DIM}-E{EMBED_SCALE}"
FILENAME_PREFIX=f"v5-hs2x-L{LAYER_COUNT}-D{EMBED_DIM}-E{EMBED_SCALE_LABEL}"

print("DEEPSPEED_STRAT:", DEEPSPEED_STRAT)
print("ENABLE_WANDB:", ENABLE_WANDB)
print("GPU_DEVICES:", GPU_DEVICES)

if ENABLE_WANDB:
    WANDB_MODE="online"
else:
    WANDB_MODE="disabled"

# Computing the notebook, and various paths
import os
NOTEBOOK_DIR=os.path.dirname(os.path.abspath("__file__"))
PROJECT_DIR=os.path.abspath(os.path.join(NOTEBOOK_DIR, "../../../../"))
TRAINER_DIR=os.path.abspath(os.path.join(PROJECT_DIR, "./RWKV-v5headsize2x/"))
INFERENCE_DIR=os.path.abspath(os.path.join(PROJECT_DIR, "./RWKV-v5headsize2x/"))

print("NOTEBOOK_DIR:", NOTEBOOK_DIR)
print("INFERENCE_DIR:", INFERENCE_DIR)
print("TRAINER_DIR:", TRAINER_DIR)
print("PROJECT_DIR:", PROJECT_DIR)

DEEPSPEED_STRAT: deepspeed_stage_2_offload
ENABLE_WANDB: True
GPU_DEVICES: auto
NOTEBOOK_DIR: /actions-runner/_work/RWKV-infctx-trainer/RWKV-infctx-trainer/notebook/experiment/rwkv-x-exp/v5-headsize2x
INFERENCE_DIR: /actions-runner/_work/RWKV-infctx-trainer/RWKV-infctx-trainer/RWKV-v5headsize2x
TRAINER_DIR: /actions-runner/_work/RWKV-infctx-trainer/RWKV-infctx-trainer/RWKV-v5headsize2x
PROJECT_DIR: /actions-runner/_work/RWKV-infctx-trainer/RWKV-infctx-trainer


In [4]:
# Init the model
!cd "{TRAINER_DIR}" && \
    export RWKV_WAVENET_LAYERS="{RWKV_WAVENET_LAYERS}" && \
    python3 ./init_model.py \
        --n_layer 6 --n_embd 4096 \
        --emb-scale "{EMBED_SCALE}" \
        --vocab_size neox --skip-if-exists \
        "../model/L{LAYER_COUNT}-D{EMBED_DIM}-E{EMBED_SCALE_LABEL}-neox-v5base-init.pth"

Setting ds_accelerator to cuda (auto detect)


[RWKV.model] Running RWKV model using 'torch-jit' with torch '2.0.1+cu118'
---- Initializing model ----
No of layers: 6
Embedding size: 4096
Output model path: ../model/L6-D4096-E0_1-neox-v5base-init.pth
Vocab size: 50277
Emb scale: 0.1
Note: this process takes a significant time (and ram) for large models
---- ----- ----


50277 4096  -0.1 emb.weight


4096  4096  1.0  blocks.0.att.receptance.weight


4096  4096  1.0  blocks.0.att.key.weight


...

4096  4096  1.0  blocks.5.att.key.weight


4096  4096  1.0  blocks.5.att.value.weight


4096  4096  0    blocks.5.att.output.weight
16384 4096  1.0  blocks.5.ffn.key.weight


4096  4096  0    blocks.5.ffn.receptance.weight
4096  16384 0    blocks.5.ffn.value.weight


50277 4096  0.5  head.weight


## Enwiki Stage 1 : Foundation 4k model training

In [5]:
# Lets preload the requried dataset 
!cd "{TRAINER_DIR}" && \
    python3 preload_datapath.py "{NOTEBOOK_DIR}/v5base-enwiki-4k.yaml"

Traceback (most recent call last):
  File "/actions-runner/_work/RWKV-infctx-trainer/RWKV-infctx-trainer/RWKV-v5headsize2x/preload_datapath.py", line 37, in <module>
    dataMod.prepare_data()
  File "/actions-runner/_work/RWKV-infctx-trainer/RWKV-infctx-trainer/RWKV-v5headsize2x/src/data.py", line 465, in prepare_data
    prepare_data_static(**self._init_locals)
  File "/actions-runner/_work/RWKV-infctx-trainer/RWKV-infctx-trainer/RWKV-v5headsize2x/src/data.py", line 94, in prepare_data_static
    src_dataset = load_dataset(**load_dataset_params)
                  ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/usr/local/lib/python3.11/dist-packages/datasets/load.py", line 1785, in load_dataset
    builder_instance = load_dataset_builder(
                       ^^^^^^^^^^^^^^^^^^^^^
  File "/usr/local/lib/python3.11/dist-packages/datasets/load.py", line 1514, in load_dataset_builder
    dataset_module = dataset_module_factory(
                     ^^^^^^^^^^^^^^^^^^^^^^^
  File "/usr/loc

In [6]:
# Start the foundation model training
!cd "{TRAINER_DIR}" && \
    export RWKV_WAVENET_LAYERS="{RWKV_WAVENET_LAYERS}" && \
    export WANDB_MODE="{WANDB_MODE}" && \
    python lightning_trainer.py fit \
        -c "{NOTEBOOK_DIR}/v5base-enwiki-4k.yaml" \
        --trainer.logger.init_args.name="{WANDB_PREFIX} - Enwiki-4k Foundation (train-ctx=4k, {DEEPSPEED_STRAT})" \
        --trainer.strategy="{DEEPSPEED_STRAT}" \
        --trainer.devices="{GPU_DEVICES}" \
        --trainer.callbacks.init_args.dirpath="../checkpoint/{FILENAME_PREFIX}-enwiki-4k/" \
        --model.load_model="../model/L{LAYER_COUNT}-D{EMBED_DIM}-E{EMBED_SCALE_LABEL}-neox-v5base-init.pth" \
        --model.ctx_len=4096 \
        --model.bptt_learning_range=1

Setting ds_accelerator to cuda (auto detect)


[RWKV.model] Running RWKV model using 'torch-jit' with torch '2.0.1+cu118'


/usr/local/lib/python3.11/dist-packages/lightning/pytorch/cli.py:484: UserWarning: LightningCLI's args parameter is intended to run from within Python like if it were from the command line. To prevent mistakes it is not recommended to provide both args and command line arguments, got: sys.argv[1:]=['fit', '-c', '/actions-runner/_work/RWKV-infctx-trainer/RWKV-infctx-trainer/notebook/experiment/rwkv-x-exp/v5-headsize2x/v5base-enwiki-4k.yaml', '--trainer.logger.init_args.name=v5-hs2x-L6-D4096-E0.1 - Enwiki-4k Foundation (train-ctx=4k, deepspeed_stage_2_offload)', '--trainer.strategy=deepspeed_stage_2_offload', '--trainer.devices=auto', '--trainer.callbacks.init_args.dirpath=../checkpoint/v5-hs2x-L6-D4096-E0_1-enwiki-4k/', '--model.load_model=../model/L6-D4096-E0_1-neox-v5base-init.pth', '--model.ctx_len=4096', '--model.bptt_learning_range=1'], args=['fit', '-c', '/actions-runner/_work/RWKV-infctx-trainer/RWKV-infctx-trainer/notebook/experiment/rwkv-x-exp/v5-headsize2x/v5base-enwiki-4k.yam

/usr/local/lib/python3.11/dist-packages/lightning/fabric/utilities/seed.py:39: UserWarning: No seed found, seed set to 2838735928
  rank_zero_warn(f"No seed found, seed set to {seed}")
Global seed set to 2838735928


wandb: Currently logged in as: picocreator (rwkv-x-dev). Use `wandb login --relogin` to force relogin


...

Validation DataLoader 0: 100%|██████████████████| 52/52 [00:21<00:00,  2.41it/s]

Epoch 0: 100%|█| 10186/10186 [10:23:59<00:00,  3.68s/it, v_num=sswf, train/loss=
Epoch 0: 100%|█| 10186/10186 [10:23:59<00:00,  3.68s/it, v_num=sswf, train/loss=

`Trainer.fit` stopped: `max_epochs=1` reached.
Epoch 0: 100%|█| 10186/10186 [10:24:14<00:00,  3.68s/it, v_num=sswf, train/loss=


wandb: Waiting for W&B process to finish... (success).


wandb: 
wandb: Run history:
wandb:              batchidx ▁▁▁▂▂▂▂▂▂▃▃▃▃▃▄▄▄▄▄▄▅▅▅▅▅▅▆▆▆▆▆▇▇▇▇▇▇███
wandb:                 epoch ▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁
wandb:           global_rank ▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁
wandb:          real_ctx_len ▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁
wandb:               substep ▁▁▁▂▂▂▂▂▂▃▃▃▃▃▄▄▄▄▄▄▅▅▅▅▅▅▆▆▆▆▆▇▇▇▇▇▇███
wandb:            train/loss █▆▆▅▅▅▄▅▄▅▃▄▄▄▄▄▃▄▃▃▃▃▃▂▄▃▃▄▂▂▂▁▂▂▃▃▃▃▃▂
wandb:   trainer/global_step ▁▁▁▂▂▂▂▂▂▃▃▃▃▃▃▄▄▄▄▄▅▅▅▅▅▅▆▆▆▆▆▆▇▇▇▇▇███
wandb: trainer/learning_rate ███▇▇▇▇▇▇▆▆▆▆▆▅▅▅▅▅▅▄▄▄▄▄▄▃▃▃▃▃▂▂▂▂▂▂▁▁▁
wandb:       validation/loss ▁
wandb: 
wandb: Run summary:
wandb:              batchidx 51
wandb:                 epoch 0
wandb:           global_rank 0
wandb:          real_ctx_len 4095
wandb:               substep 408
wandb:            train/loss 4.09375
wandb:   trainer/global_step 2546
wandb: trainer/learning_rate 0.0004
wandb:       validation/loss 3.81442
wandb: 
wandb: 🚀 View run v5-hs2x-L6-D4096-E0.1 

In [7]:
# Lets export the model from the checkpoint
!cd "{TRAINER_DIR}" && \
    python export_checkpoint.py "../checkpoint/{FILENAME_PREFIX}-enwiki-4k/last.ckpt" "../model/{FILENAME_PREFIX}-enwiki-4k.pth" "bf16"
!cd "{TRAINER_DIR}" && ls -alh "../model/{FILENAME_PREFIX}-enwiki-4k.pth"

Setting ds_accelerator to cuda (auto detect)


Processing zero checkpoint '../checkpoint/v5-hs2x-L6-D4096-E0_1-enwiki-4k/last.ckpt/checkpoint'


Detected checkpoint of type zero stage ZeroStageEnum.gradients, world_size: 8


Parsing checkpoint created by deepspeed==0.9.3


Reconstructed fp32 state dict with 126 params 1720779136 elements
Saving bf16 state dict to ../model/v5-hs2x-L6-D4096-E0_1-enwiki-4k.pth


-rw-r--r-- 1 root root 3.3G Aug 23 22:00 ../model/v5-hs2x-L6-D4096-E0_1-enwiki-4k.pth


In [8]:
# # Lets do a quick dragon prompt validation
!cd "{INFERENCE_DIR}" && \
    export RWKV_WAVENET_LAYERS="{RWKV_WAVENET_LAYERS}" && \
    python3 dragon_test.py "../model/{FILENAME_PREFIX}-enwiki-4k.pth" "cuda fp32"

Setting ds_accelerator to cuda (auto detect)


[RWKV.model] Running RWKV model using 'torch-jit' with torch '2.0.1+cu118'


--- DRAGON PROMPT ---
In a shocking finding, scientist discovered a herd of dragons living in a remote, previously unexplored valley, in Tibet. Even more surprising to the researchers was the fact that the dragons spoke perfect Chinese.

In

 2018

...

na

 in

 Hindu

ism

.

In [9]:
# Lets do a quick memory test
!export RWKV_WAVENET_LAYERS="{RWKV_WAVENET_LAYERS}" && \
        python3 ../memory_script/eval_v5_memory_guided.py "{PROJECT_DIR}/model/{FILENAME_PREFIX}-enwiki-4k.pth"

Setting ds_accelerator to cuda (auto detect)


[RWKV.model] Running RWKV model using 'torch-jit' with torch '2.0.1+cu118'


Traceback (most recent call last):
  File "/actions-runner/_work/RWKV-infctx-trainer/RWKV-infctx-trainer/notebook/experiment/rwkv-x-exp/v5-headsize2x/../memory_script/eval_v5_memory_guided.py", line 366, in <module>
    asyncio.run(main_function())
  File "/usr/lib/python3.11/asyncio/runners.py", line 190, in run
    return runner.run(main)
           ^^^^^^^^^^^^^^^^
  File "/usr/lib/python3.11/asyncio/runners.py", line 118, in run
    return self._loop.run_until_complete(task)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/usr/lib/python3.11/asyncio/base_events.py", line 653, in run_until_complete
    return future.result()
           ^^^^^^^^^^^^^^^
  File "/actions-runner/_work/RWKV-infctx-trainer/RWKV-infctx-trainer/notebook/experiment/rwkv-x-exp/v5-headsize2x/../memory_script/eval_v5_memory_guided.py", line 58, in main_function
    model = SimpleRWKV(model_path, device="cuda")
            ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/actions-runner/_work/RWKV-infctx-tra

# Enwiki Stage 2 : Basic Instruct Tuning

In [10]:
# Lets preload the requried dataset
!cd "{TRAINER_DIR}" && \
    python3 preload_datapath.py "{NOTEBOOK_DIR}/v5base-enwiki-instruct.yaml"


Extracting data files: 100%|████████████████████| 1/1 [00:00<00:00, 1381.98it/s]
Setting num_proc from 64 back to 1 for the train split to disable multiprocessing as it only contains one shard.
Generating train split:   0%|                  | 0/15015 [00:00<?, ? examples/s]

Dataset parquet downloaded and prepared to /actions-runner/.cache/huggingface/datasets/c-s-ale___parquet/c-s-ale--dolly-15k-instruction-alpaca-format-9dfbb23260d63d9d/0.0.0/14a00e99c0d15a23649d0db8944380ac81082d4b021f398733dd84f3a6c569a7. Subsequent calls will reuse this data.
100%|████████████████████████████████████████████| 1/1 [00:00<00:00, 653.11it/s]


Map (num_proc=64):   0%|                       | 0/15015 [00:00<?, ? examples/s]

Map (num_proc=64):   0%|             | 70/15015 [00:00<00:45, 328.44 examples/s]

Map (num_proc=64):   4%|▍          | 555/15015 [00:00<00:07, 1933.18 examples/s]

...

Filter (num_proc=64):   0%|                    | 0/15015 [00:00<?, ? examples/s]

Filter (num_proc=64):   2%|▏       | 235/15015 [00:00<00:07, 1983.84 examples/s]

Filter (num_proc=64):  25%|█▌    | 3760/15015 [00:00<00:00, 20035.61 examples/s]

Filter (num_proc=64):  63%|███▊  | 9398/15015 [00:00<00:00, 35849.93 examples/s]

Saving the dataset (0/1 shards):   0%|         | 0/14932 [00:00<?, ? examples/s]

In [11]:
# Start the instruct finetuning
!cd "{TRAINER_DIR}" && \
    export WANDB_MODE="{WANDB_MODE}" && \
    export RWKV_WAVENET_LAYERS="{RWKV_WAVENET_LAYERS}" && \
    python lightning_trainer.py fit \
        -c "{NOTEBOOK_DIR}/v5base-enwiki-instruct.yaml" \
        --trainer.logger.init_args.name="{WANDB_PREFIX} - Enwiki-Instruct (train-ctx=4k, {DEEPSPEED_STRAT})" \
        --trainer.strategy="{DEEPSPEED_STRAT}" \
        --trainer.devices="{GPU_DEVICES}" \
        --trainer.callbacks.init_args.dirpath="../checkpoint/{FILENAME_PREFIX}-enwiki-instruct/" \
        --model.load_model="../model/{FILENAME_PREFIX}-enwiki-4k.pth" \
        --model.ctx_len=4096 \
        --model.bptt_learning_range=1

Setting ds_accelerator to cuda (auto detect)


[RWKV.model] Running RWKV model using 'torch-jit' with torch '2.0.1+cu118'


/usr/local/lib/python3.11/dist-packages/lightning/pytorch/cli.py:484: UserWarning: LightningCLI's args parameter is intended to run from within Python like if it were from the command line. To prevent mistakes it is not recommended to provide both args and command line arguments, got: sys.argv[1:]=['fit', '-c', '/actions-runner/_work/RWKV-infctx-trainer/RWKV-infctx-trainer/notebook/experiment/rwkv-x-exp/v5-headsize2x/v5base-enwiki-instruct.yaml', '--trainer.logger.init_args.name=v5-hs2x-L6-D4096-E0.1 - Enwiki-Instruct (train-ctx=4k, deepspeed_stage_2_offload)', '--trainer.strategy=deepspeed_stage_2_offload', '--trainer.devices=auto', '--trainer.callbacks.init_args.dirpath=../checkpoint/v5-hs2x-L6-D4096-E0_1-enwiki-instruct/', '--model.load_model=../model/v5-hs2x-L6-D4096-E0_1-enwiki-4k.pth', '--model.ctx_len=4096', '--model.bptt_learning_range=1'], args=['fit', '-c', '/actions-runner/_work/RWKV-infctx-trainer/RWKV-infctx-trainer/notebook/experiment/rwkv-x-exp/v5-headsize2x/v5base-enwik

/usr/local/lib/python3.11/dist-packages/lightning/fabric/utilities/seed.py:39: UserWarning: No seed found, seed set to 268901941
  rank_zero_warn(f"No seed found, seed set to {seed}")
Global seed set to 268901941


wandb: Currently logged in as: picocreator (rwkv-x-dev). Use `wandb login --relogin` to force relogin


...


Validation DataLoader 0: 100%|██████████████████| 10/10 [00:02<00:00,  4.23it/s]

Epoch 0: 100%|█| 1867/1867 [1:38:33<00:00,  3.17s/it, v_num=w6r8, train/loss=4.5
Epoch 0: 100%|█| 1867/1867 [1:38:33<00:00,  3.17s/it, v_num=w6r8, train/loss=4.5

`Trainer.fit` stopped: `max_epochs=1` reached.
Epoch 0: 100%|█| 1867/1867 [1:38:46<00:00,  3.17s/it, v_num=w6r8, train/loss=4.5


wandb: Waiting for W&B process to finish... (success).


wandb: 
wandb: Run history:
wandb:              batchidx ▁▁▁▂▂▂▂▂▂▃▃▃▃▃▄▄▄▄▄▄▅▅▅▅▅▆▆▆▆▆▇▇▇▇▇▇███▁
wandb:                 epoch ▁▁▁▁▁▁▁▁▁▁
wandb:           global_rank ▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁
wandb:          real_ctx_len ▇▂▁▂▃▂▂▂▃▂▂▅▃▁█▁▁▁▃▇▂▂▃▁▅▁▄▁▁▂▁▂▁▃▃▂▇▂▃▁
wandb:               substep ▁▁▁▂▂▂▂▂▂▃▃▃▃▃▄▄▄▄▄▄▅▅▅▅▅▆▆▆▆▆▇▇▇▇▇▇███▁
wandb:            train/loss ▅█▆▆▇▂█▃▅▄▆▆▇▂▃▅▅▅▆▅▄▄▄▃▅▆▄▅▄▆▂▄▄▁▄▃▂▅▇▇
wandb:   trainer/global_step ▁▁▁▁▂▂▂▂▂▃▃▃▃▃▃▄▄▄▄▄▅▅▅▅▅▅▆▆▆▆▆▇▇▇▇▇▇███
wandb: trainer/learning_rate ████▇▇▇▇▇▆▆▆▆▆▆▅▅▅▅▅▄▄▄▄▄▄▃▃▃▃▃▂▂▂▂▂▂▁▁▁
wandb:       validation/loss ▁
wandb: 
wandb: Run summary:
wandb:              batchidx 9
wandb:                 epoch 0
wandb:           global_rank 0
wandb:          real_ctx_len 85
wandb:               substep 72
wandb:            train/loss 4.21875
wandb:   trainer/global_step 466
wandb: trainer/learning_rate 0.0003
wandb:       validation/loss 3.42412
wandb: 
wandb: 🚀 View run v5-hs2x-L6-D4096-E0.1 - Enwiki-Instruct (train-ctx=4k, de

In [12]:
# Lets export the model from the checkpoint
!cd "{TRAINER_DIR}" && \
    python export_checkpoint.py "../checkpoint/{FILENAME_PREFIX}-enwiki-instruct/last.ckpt" "../model/{FILENAME_PREFIX}-enwiki-instruct.pth" "bf16"
!cd "{TRAINER_DIR}" && ls -alh "../model/{FILENAME_PREFIX}-enwiki-instruct.pth"

Setting ds_accelerator to cuda (auto detect)


Processing zero checkpoint '../checkpoint/v5-hs2x-L6-D4096-E0_1-enwiki-instruct/last.ckpt/checkpoint'


Detected checkpoint of type zero stage ZeroStageEnum.gradients, world_size: 8


Parsing checkpoint created by deepspeed==0.9.3


Reconstructed fp32 state dict with 126 params 1720779136 elements
Saving bf16 state dict to ../model/v5-hs2x-L6-D4096-E0_1-enwiki-instruct.pth


-rw-r--r-- 1 root root 3.3G Aug 23 23:44 ../model/v5-hs2x-L6-D4096-E0_1-enwiki-instruct.pth


In [13]:
# # Lets do a quick dragon prompt validation
!cd "{INFERENCE_DIR}" && \
    export RWKV_WAVENET_LAYERS="{RWKV_WAVENET_LAYERS}" && \
    python3 dragon_test.py "../model/{FILENAME_PREFIX}-enwiki-instruct.pth" "cuda fp32"

Setting ds_accelerator to cuda (auto detect)


[RWKV.model] Running RWKV model using 'torch-jit' with torch '2.0.1+cu118'


--- DRAGON PROMPT ---
In a shocking finding, scientist discovered a herd of dragons living in a remote, previously unexplored valley, in Tibet. Even more surprising to the researchers was the fact that the dragons spoke perfect Chinese.

 The

 finding

...

 a

 tree

.

 I

 had


In [14]:
# Lets do a quick memory test
!export RWKV_WAVENET_LAYERS="{RWKV_WAVENET_LAYERS}" && \
        python3 ../memory_script/eval_v5_memory_guided.py "{PROJECT_DIR}/model/{FILENAME_PREFIX}-enwiki-instruct.pth"

Setting ds_accelerator to cuda (auto detect)


[RWKV.model] Running RWKV model using 'torch-jit' with torch '2.0.1+cu118'


Traceback (most recent call last):
  File "/actions-runner/_work/RWKV-infctx-trainer/RWKV-infctx-trainer/notebook/experiment/rwkv-x-exp/v5-headsize2x/../memory_script/eval_v5_memory_guided.py", line 366, in <module>
    asyncio.run(main_function())
  File "/usr/lib/python3.11/asyncio/runners.py", line 190, in run
    return runner.run(main)
           ^^^^^^^^^^^^^^^^
  File "/usr/lib/python3.11/asyncio/runners.py", line 118, in run
    return self._loop.run_until_complete(task)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/usr/lib/python3.11/asyncio/base_events.py", line 653, in run_until_complete
    return future.result()
           ^^^^^^^^^^^^^^^
  File "/actions-runner/_work/RWKV-infctx-trainer/RWKV-infctx-trainer/notebook/experiment/rwkv-x-exp/v5-headsize2x/../memory_script/eval_v5_memory_guided.py", line 58, in main_function
    model = SimpleRWKV(model_path, device="cuda")
            ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/actions-runner/_work/RWKV-infctx-tra